# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [TRPO]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import TRPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.21.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.21.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.21.0\n')
wandb, version 0.13.3


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 65% average battery) 
#case = 'wohnblock_household_simulation_adaptive_18.yaml' #(18 EVs arrivals per week with 40% average battery) 
#case = 'wohnblock_household_simulation_adaptive_22.yaml' #(22 EVs arrivals per week with 55% average battery)

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f9ff95b1250>Mean parking time: 23.9
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.9, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energy

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21838.24 , over-consume=kWh  38907.1 , under-consume=kWh  17068.86 , Total_cost=€  909.7 , overcost=€  1387.2 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

In [ ]:
env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/TRPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/TRPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="TRPO_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/TRPO_models/model_TRPO_"

model_id = "2ydih28d"
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21290.63 , over-consume=kWh  38971.4 , under-consume=kWh  17680.77 , Total_cost=€  872.99 , overcost=€  1381.18 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5266.51 , over-consume=KWh  1601.17 , under-consume=KWh  6867.68 , Total_cost=€  -113.22 , Overcost=€  54.8 
 EV_INFO: Av.EV_energy_leaving=kWh  65.4 , Std.EV_energy_leaving=kWh  26.69 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 357075.14 - Step_rewars (load_t= 332644.45, EVs_energy_t= 1799.73)
 - Final_rewards (EVs_energy= 14562.6, Overconsume= -860.64, Underconsume= -3532.99, Overcost= 12461.99)
Episode:1 Score:357075.1359652777


In [ ]:
env.plot_VPP_energies()

In [ ]:
VPP_table.head(15000)

0          1          2          3              EVs_id  \
time                                                                            
2022-01-01 00:00:00  0.0   0.000000  40.897972   0.000000        [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0   0.000000  40.197933   0.000000     [0, 0, 3129, 0]   
2022-01-01 00:30:00  0.0   0.000000  39.622128   0.000000     [0, 0, 3129, 0]   
2022-01-01 00:45:00  0.0   0.000000  39.035473   0.000000     [0, 0, 3129, 0]   
2022-01-01 01:00:00  0.0   0.000000  38.609863   0.000000     [0, 0, 3129, 0]   
...                  ...        ...        ...        ...                 ...   
2022-06-06 04:45:00  0.0  75.698875   0.000000  76.847649  [0, 3579, 0, 3580]   
2022-06-06 05:00:00  0.0  77.159737   0.000000  78.308510  [0, 3579, 0, 3580]   
2022-06-06 05:15:00  0.0  78.735298   0.000000  79.884071  [0, 3579, 0, 3580]   
2022-06-06 05:30:00  0.0  80.401443   0.000000  81.550217  [0, 3579, 0, 3580]   
2022-06-06 05:45:00  0.0  81.967377   0.000000  83.116150  [0, 3579, 0, 3580]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [2, 0, 2, 2]  [False, True, False, False]  1.710441   
2022-01-01 00:15:00  [2, 0, 2, 2]   [False, True, True, False]  0.000000   
2022-01-01 00:30:00  [2, 0, 2, 2]   [False, True, True, False]  0.000000   
2022-01-01 00:45:00  [2, 0, 2, 2]   [False, True, True, False]  0.000000   
2022-01-01 01:00:00  [2, 0, 2, 2]   [False, True, True, False]  0.000000   
...                           ...                          ...       ...   
2022-06-06 04:45:00  [0, 1, 0, 1]     [True, True, True, True]  0.000000   
2022-06-06 05:00:00  [0, 1, 2, 1]    [True, True, False, True]  0.000000   
2022-06-06 05:15:00  [0, 1, 2, 1]    [True, True, False, True]  0.000000   
2022-06-06 05:30:00  [0, 1, 2, 1]    [True, True, False, True]  0.000000   
2022-06-06 05:45:00  [0, 1, 2, 1]    [True, True, False, True]  0.000000   

                     load_reward  EV_reward   rewards  
time                                                   
2022-01-01 00:00:00     15.00000        0.0  15.00000  
2022-01-01 00:15:00     15.00000        0.0  15.00000  
2022-01-01 00:30:00     15.00000        0.0  15.00000  
2022-01-01 00:45:00     15.00000        0.0  15.00000  
2022-01-01 01:00:00     14.52397        0.0  14.52397  
...                          ...        ...       ...  
2022-06-06 04:45:00     15.00000        0.0  15.00000  
2022-06-06 05:00:00     15.00000        0.0  15.00000  
2022-06-06 05:15:00     15.00000        0.0  15.00000  
2022-06-06 05:30:00     15.00000        0.0  15.00000  
2022-06-06 05:45:00     15.00000        0.0  15.00000  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 02:15:00, Parking_time: 24, Leaving_time: 2022-01-02 02:15:00, SOC: 0.4526197752533386, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 21:15:00, Parking_time: 23.73159408401372, Leaving_time: 2023-01-01 20:58:53.738702, SOC: 0.35966767213588446, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12520.29 , over-consume=kWh  33651.09 , under-consume=kWh  21130.8 , Total_cost=€  588.16 , overcost=€  1444.11 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11908.39 , over-consume=kWh  34152.41 , under-consume=kWh  22244.02 , Total_cost=€  608.28 , overcost=€  1514.2 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7956.06 , over-consume=KWh  1231.83 , under-consume=KWh  9187.89 , Total_cost=€  -300.21 , Overcost=€  53.49 
 EV_INFO: Av.EV_energy_leaving=kWh  71.33 , Std.EV_energy_leaving=kWh  27.04 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 353706.32 - Step_rewars (load_t= 311457.27, EVs_energy_t= 15987.91)
 - Final_rewards (EVs_energy= 17623.18, Overconsume= -655.86, Underconsume= -3994.68, Overcost= 13288.49)
Episode:1 Score:353706.31531876745


In [ ]:
env.plot_VPP_energies()

In [ ]:
VPP_table.head(15000)

0    1    2    3        EVs_id       actions  \
time                                                                  
2022-01-01 00:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [1, 0, 2, 1]   
...                  ...  ...  ...  ...           ...           ...   
2022-06-06 04:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [0, 0, 2, 1]   
2022-06-06 05:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [0, 0, 2, 1]   
2022-06-06 05:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [0, 0, 2, 1]   
2022-06-06 05:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [0, 0, 2, 1]   
2022-06-06 05:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [0, 0, 2, 1]   

                                      mask_truth       load  load_reward  \
time                                                                       
2022-01-01 00:00:00  [False, True, False, False]  -3.356737    -5.145021   
2022-01-01 00:15:00  [False, True, False, False]  -4.159523    -4.718350   
2022-01-01 00:30:00  [False, True, False, False]  -3.831010    -3.389162   
2022-01-01 00:45:00  [False, True, False, False]  -3.033497    -5.098325   
2022-01-01 01:00:00  [False, True, False, False]  -4.108158    -4.821584   
...                                          ...        ...          ...   
2022-06-06 04:45:00   [True, True, False, False] -11.243047   -13.778966   
2022-06-06 05:00:00   [True, True, False, False] -13.656863   -14.114637   
2022-06-06 05:15:00   [True, True, False, False] -14.026100   -14.099258   
2022-06-06 05:30:00   [True, True, False, False] -14.009183   -14.554993   
2022-06-06 05:45:00   [True, True, False, False] -14.510492   -16.039442   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.145021  
2022-01-01 00:15:00        0.0  -4.718350  
2022-01-01 00:30:00        0.0  -3.389162  
2022-01-01 00:45:00        0.0  -5.098325  
2022-01-01 01:00:00        0.0  -4.821584  
...                        ...        ...  
2022-06-06 04:45:00        0.0 -13.778966  
2022-06-06 05:00:00        0.0 -14.114637  
2022-06-06 05:15:00        0.0 -14.099258  
2022-06-06 05:30:00        0.0 -14.554993  
2022-06-06 05:45:00        0.0 -16.039442  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 02:15:00, Parking_time: 22.986512870609562, Leaving_time: 2022-01-02 01:14:11.446334, SOC: 0.5272320339241312, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 20:15:00, Parking_time: 24, Leaving_time: 2023-01-01 20:15:00, SOC: 0.5687415111325865, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8880.6 , over-consume=kWh  32401.85 , under-consume=kWh  23521.25 , Total_cost=€  502.56 , overcost=€  1360.01 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7225.77 , over-consume=kWh  30979.73 , under-consume=kWh  23753.96 , Total_cost=€  430.22 , overcost=€  1304.01 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9332.91 , over-consume=KWh  1175.62 , under-consume=KWh  10508.53 , Total_cost=€  -330.22 , Overcost=€  47.57 
 EV_INFO: Av.EV_energy_leaving=kWh  74.2 , Std.EV_energy_leaving=kWh  25.75 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 348049.66 - Step_rewars (load_t= 296341.02, EVs_energy_t= 25617.27)
 - Final_rewards (EVs_energy= 18300.44, Overconsume= -732.57, Underconsume= -4544.82, Overcost= 13068.33)
Episode:1 Score:348049.6588939131


In [ ]:
env.plot_VPP_energies()

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  78.069954  49.745785  96.879387  87.779976   
2022-06-06 03:45:00  78.462685  49.495785  97.272118  88.172707   
2022-06-06 04:00:00  79.112915  49.245785  97.922348  88.822937   
2022-06-06 04:15:00  79.780647  48.995785  98.590080  89.490669   
2022-06-06 04:30:00  80.431885  48.745785  99.241318  90.141907   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
...                                       ...           ...   
2022-06-06 03:30:00  [9827, 9825, 9826, 9828]  [1, 2, 1, 1]   
2022-06-06 03:45:00  [9827, 9825, 9826, 9828]  [1, 2, 1, 1]   
2022-06-06 04:00:00  [9827, 9825, 9826, 9828]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [9827, 9825, 9826, 9828]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [9827, 9825, 9826, 9828]  [1, 2, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, True, False, False] -3.999030e+00    -4.936781   
2022-01-01 00:15:00  [False, True, False, False] -3.962069e+00    -2.980116   
2022-01-01 00:30:00  [False, True, False, False] -2.788070e+00    -4.535527   
2022-01-01 00:45:00  [False, True, False, False] -3.721316e+00    -5.768481   
2022-01-01 01:00:00  [False, True, False, False] -4.845329e+00    -5.921395   
...                                          ...           ...          ...   
2022-06-06 03:30:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 03:45:00   [True, False, False, True]  4.440892e-16    15.000000   
2022-06-06 04:00:00   [True, False, False, True] -8.881784e-16    15.000000   
2022-06-06 04:15:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 04:30:00   [True, False, False, True]  0.000000e+00    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.936781  
2022-01-01 00:15:00        0.0  -2.980116  
2022-01-01 00:30:00        0.0  -4.535527  
2022-01-01 00:45:00        0.0  -5.768481  
2022-01-01 01:00:00        0.0  -5.921395  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

In [ ]:
#env.close()